In [1]:
import osmnx as ox
import pandas as pd
import folium
from shapely.geometry import Point, Polygon, MultiPolygon

In [2]:
# Get the coordinates for Dublin, Ireland
location = ox.geocode('Dublin, Ireland')

In [3]:
location

(53.3498006, -6.2602964)

In [4]:
# Use OpenStreetMaps library to get all the public suervice spots within a specified distance
distance = 25000  # Radius of 25 kilometers around the location
tags = {'amenity': True}
gdf = ox.geometries_from_point(location, tags=tags, dist=distance)

In [5]:
gdf.head()

access    amenity     created_by  fee  parking  \
element_type osmid                                                      
node         29403586     yes    parking  Potlatch 0.5d   no  surface   
             59998053     NaN  recycling            NaN  NaN      NaN   
             78514742     NaN   post_box            NaN  NaN      NaN   
             78514747     NaN        atm            NaN  NaN      NaN   
             107986833    NaN   post_box            NaN  NaN      NaN   

                                         geometry recycling:glass  \
element_type osmid                                                  
node         29403586   POINT (-6.29177 53.17470)             NaN   
             59998053   POINT (-6.32597 53.29687)             yes   
             78514742   POINT (-6.31990 53.29923)             NaN   
             78514747   POINT (-6.32149 53.29920)             NaN   
             107986833  POINT (-6.31012 53.31284)             NaN   

                       recycling_type operator operator:wikidata  ...  \
element_type osmid                                                ...   
node         29403586             NaN      NaN               NaN  ...   
             59998053       container      NaN               NaN  ...   
             78514742             NaN  An Post           Q482490  ...   
             78514747             NaN      NaN               NaN  ...   
             107986833            NaN  An Post           Q482490  ...   

                       check_date:fee rooms trade building:levels:underground  \
element_type osmid                                                              
node         29403586             NaN   NaN   NaN                         NaN   
             59998053             NaN   NaN   NaN                         NaN   
             78514742             NaN   NaN   NaN                         NaN   
             78514747             NaN   NaN   NaN                         NaN   
             107986833            NaN   NaN   NaN                         NaN   

                       abandoned building:shape recycling:aggregate  \
element_type osmid                                                    
node         29403586        NaN            NaN                 NaN   
             59998053        NaN            NaN                 NaN   
             78514742        NaN            NaN                 NaN   
             78514747        NaN            NaN                 NaN   
             107986833       NaN            NaN                 NaN   

                       old_name:1925 heating fee:covid19  
element_type osmid                                        
node         29403586            NaN     NaN         NaN  
             59998053            NaN     NaN         NaN  
             78514742            NaN     NaN         NaN  
             78514747            NaN     NaN         NaN  
             107986833           NaN     NaN         NaN  

[5 rows x 666 columns]

In [6]:
gdf['amenity'].unique()

array(['parking', 'recycling', 'post_box', 'atm', 'pub', 'fuel', 'police',
       'cinema', 'pharmacy', 'fast_food', 'social_facility',
       'community_centre', 'bicycle_parking', 'post_office', 'fountain',
       'restaurant', 'nightclub', 'cafe', 'arts_centre', 'theatre',
       'parking_entrance', 'drinking_water', 'events_venue',
       'kindergarten', 'bank', 'childcare', 'toilets', 'library',
       'bicycle_rental', 'marketplace', 'car_wash', 'car_rental', 'taxi',
       'bar', 'place_of_worship', 'studio', 'dentist', 'doctors', 'bench',
       'box_office', 'waste_basket', 'internet_cafe', 'telephone',
       'college', 'casino', 'veterinary', 'clinic', 'shelter', 'clock',
       'internet_access', 'school', 'charging_station', 'vending_machine',
       'music_school', 'training', 'stripclub', 'courthouse',
       'language_school', 'funeral_hall', 'parking_space',
       'conference_centre', 'grave_yard', 'loading_dock', 'monastery',
       'public_bookcase', 'ice_cream', 'h

In [8]:
public_services_tags = ['school', 'pharmacy', 'place_of_worship', 'bank', 'doctors', 'kindergarten', 'social_facility', 
                        'post_office', 'clinic', 'childcare', 'library', 'police', 'veterinary', 'nursing_home', 'post_depot', 
                        'fire_station', 'courthouse']

In [9]:
# Filter the data for the public service spots in the same 25 Km radius
public_services = gdf[gdf['amenity'].isin(public_services_tags)]

In [10]:
len(public_services)

3186

In [12]:
public_services.shape

(3186, 666)

In [13]:
public_services = pd.DataFrame(public_services)

# Remove all the columns which have less than 10% of the records populated
selected_columns = public_services.columns[public_services.count() > 0.1*len(public_services)]
filtered_data = public_services[selected_columns]

In [14]:
filtered_data.shape

(3186, 24)

In [15]:
filtered_data.head()

amenity                   geometry  \
element_type osmid                                                   
node         243783190           police  POINT (-6.35799 53.34473)   
             254952173         pharmacy  POINT (-6.42261 53.34785)   
             263367948  social_facility  POINT (-6.42324 53.34895)   
             278018000      post_office  POINT (-6.31741 53.28286)   
             278290761         pharmacy  POINT (-6.31806 53.28300)   

                              operator operator:wikidata operator:wikipedia  \
element_type osmid                                                            
node         243783190  Garda Síochána          Q1366959  en:Garda Síochána   
             254952173             NaN               NaN                NaN   
             263367948             NaN               NaN                NaN   
             278018000         An Post           Q482490         en:An Post   
             278290761             NaN               NaN                NaN   

                       drive_through                       name  \
element_type osmid                                                
node         243783190           NaN  Ballyfermot Garda Station   
             254952173            no           Foley's Pharmacy   
             263367948           NaN                        NaN   
             278018000           NaN      Knocklyon Post Office   
             278290761            no            Lloyds Pharmacy   

                           addr:street            brand brand:wikidata  ...  \
element_type osmid                                                      ...   
node         243783190             NaN              NaN            NaN  ...   
             254952173             NaN              NaN            NaN  ...   
             263367948  Ballyowen Lane  Citizens Advice       Q5122657  ...   
             278018000   Idrone Avenue          An Post        Q482490  ...   
             278290761             NaN  Lloyds Pharmacy       Q6662870  ...   

                       wheelchair addr:city                  website  \
element_type osmid                                                     
node         243783190        NaN    Dublin                      NaN   
             254952173        NaN       NaN                      NaN   
             263367948        NaN     Lucan                      NaN   
             278018000        NaN       NaN  https://www.anpost.com/   
             278290761        NaN       NaN                      NaN   

                       dispensing healthcare addr:housenumber denomination  \
element_type osmid                                                           
node         243783190        NaN        NaN              NaN          NaN   
             254952173        yes   pharmacy              NaN          NaN   
             263367948        NaN        NaN              NaN          NaN   
             278018000        NaN        NaN              NaN          NaN   
             278290761        yes   pharmacy              NaN          NaN   

                       religion building nodes  
element_type osmid                              
node         243783190      NaN      NaN   NaN  
             254952173      NaN      NaN   NaN  
             263367948      NaN      NaN   NaN  
             278018000      NaN      NaN   NaN  
             278290761      NaN      NaN   NaN  

[5 rows x 24 columns]

In [17]:
filtered_data.columns

Index(['amenity', 'geometry', 'operator', 'operator:wikidata',
       'operator:wikipedia', 'drive_through', 'name', 'addr:street', 'brand',
       'brand:wikidata', 'brand:wikipedia', 'email', 'opening_hours', 'phone',
       'wheelchair', 'addr:city', 'website', 'dispensing', 'healthcare',
       'addr:housenumber', 'denomination', 'religion', 'building', 'nodes'],
      dtype='object')

In [18]:
# Pick only the features/columns which will be useful for our analysis 
filtered_data = filtered_data[['geometry', 'amenity', 'name', 'addr:street', 'brand', 'addr:city']]

In [20]:
# Rename the column names for downstream use
filtered_data = filtered_data.rename(columns={'geometry': 'public_services_geometry', 
                                              'amenity': 'public_services_tag', 
                                              'name': 'public_services_address',
                                              'addr:street': 'public_services_street',
                                              'addr:city': 'public_services_city',
                                              'brand': 'public_services_brand_name'})

# Save the data into a CSV file
filtered_data.to_csv('03_public_service_locations.csv', index=False)

In [21]:
filtered_data.head()

public_services_geometry public_services_tag  \
element_type osmid                                                      
node         243783190  POINT (-6.35799 53.34473)              police   
             254952173  POINT (-6.42261 53.34785)            pharmacy   
             263367948  POINT (-6.42324 53.34895)     social_facility   
             278018000  POINT (-6.31741 53.28286)         post_office   
             278290761  POINT (-6.31806 53.28300)            pharmacy   

                          public_services_address public_services_street  \
element_type osmid                                                         
node         243783190  Ballyfermot Garda Station                    NaN   
             254952173           Foley's Pharmacy                    NaN   
             263367948                        NaN         Ballyowen Lane   
             278018000      Knocklyon Post Office          Idrone Avenue   
             278290761            Lloyds Pharmacy                    NaN   

                       public_services_brand_name public_services_city  
element_type osmid                                                      
node         243783190                        NaN               Dublin  
             254952173                        NaN                  NaN  
             263367948            Citizens Advice                Lucan  
             278018000                    An Post                  NaN  
             278290761            Lloyds Pharmacy                  NaN

In [22]:
len(filtered_data)

3186

In [23]:
# Get the counts of each hotspot category
filtered_data['public_services_tag'].value_counts()

school              698
place_of_worship    451
pharmacy            439
bank                271
doctors             246
kindergarten        185
social_facility     169
post_office         147
clinic              139
childcare           105
library              90
police               60
veterinary           58
post_depot           50
nursing_home         38
fire_station         23
courthouse           17
Name: public_services_tag, dtype: int64

In [24]:
# Create a map centered around Dublin
latitude = location[0]  # Latitude of the center point
longitude = location[1] # Longitude of the center point
map_osm = folium.Map(location=[latitude, longitude], zoom_start=12)
# icon = folium.Icon(icon='circle', prefix='fa', color='blue', icon_color='white', icon_size=(4, 4))

# Add markers for each charging station location
for index, spot in public_services.iterrows():
    name = spot['name']
    geometry = spot['geometry']

    # Extract latitude and longitude from the Polygon object
    if isinstance(geometry, Point):
        point = Point(geometry)
        lon = point.x
        lat = point.y
    else:
        centroid = geometry.centroid
        lon = centroid.x
        lat = centroid.y

    marker = folium.CircleMarker(location=[lat, lon], radius=4, popup=name, color='blue', fill=True, fill_color='blue')
    marker.add_to(map_osm)

# Display the map
map_osm